# Spark with Python

05-08-2023
by Thomas Johnson III

This notebook is to practice the usage of Pyspark for personal coding development. A lot of what is seen here will be extensions of existing work or methods for the loaded Python libraries that already exist.

In [54]:
# Loading in necessary modules and functions.
import numpy as np
import pandas as pd
from sklearn.datasets import make_regression
from pyspark.context import SparkContext
from pyspark.mllib.stat import Statistics
from pyspark.sql import SparkSession
from pyspark.sql.functions import col
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression, GBTRegressor
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder, TrainValidationSplit
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
from pyspark.ml.feature import PCA
import time

In [2]:
# Generate some regression data to be used for fitting and evaluation.
def gen_data():
    np.random.seed(12) # Set a random seed
    # Obtain the simulated data for regression.
    dat_x, dat_y = make_regression(n_samples = 5000, # 5000 cases
                                                   n_features = 25, # 25 variables, by default 10 are infromative.
                                                   noise = 1)
    x_names = []
    for i in range(25):
        x_names.append("X" + str(i+1)) #Get names of X columns
    # Dataframe conversion occurring
    dat_x = pd.DataFrame(dat_x, columns = x_names) 
    dat_y = pd.DataFrame(dat_y, columns = ["y"])
    return(dat_x, dat_y) # Return X and y

Now we obtain the $\boldsymbol{X}$ and $\boldsymbol{y}$ data.

In [3]:
X_dat, y_dat = gen_data() 

Combine $\boldsymbol{X}$ and \boldsymbol{y} into one dataframe. Starting in pandas then moving the dataframe into pyspark.

In [4]:
pop_data = pd.concat([X_dat,y_dat], axis = 1)

Now that we have the population data, we can start loading into Pyspark.

In [5]:
# Set up the Spark settings with 4Gb of memory. Set up a spark session to work in.
SparkContext.setSystemProperty("spark.executor.memory", "4g")
sp_context = SparkSession.builder.master("local[1]").appName("ml_spark").getOrCreate()

23/05/08 15:03:16 WARN Utils: Your hostname, revenant-desktop resolves to a loopback address: 127.0.1.1; using 192.168.50.43 instead (on interface wlp5s0)
23/05/08 15:03:16 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/05/08 15:03:17 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [6]:
# Move pandas dataframe to Spark in memory
pop_data_sp = sp_context.createDataFrame(pop_data)

In [7]:
# Calculate some brief summary statistics.
pop_data_sp.select(pop_data_sp.columns[1:5]).summary().show()

23/05/08 15:03:23 WARN package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.
23/05/08 15:03:24 WARN TaskSetManager: Stage 0 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


+-------+--------------------+--------------------+--------------------+--------------------+
|summary|                  X2|                  X3|                  X4|                  X5|
+-------+--------------------+--------------------+--------------------+--------------------+
|  count|                5000|                5000|                5000|                5000|
|   mean|-0.01210631494364...|-8.85369555971085...|-0.00268963742477...|-0.02023292955390...|
| stddev|  0.9957392741360688|   1.006254205754425|  1.0083556524718054|  1.0015132191307523|
|    min| -3.4157248243589216|  -3.654432921988915| -3.5675804306862626| -3.8897380263174064|
|    25%|  -0.676277675641535| -0.6825850313187773| -0.6808199601427417| -0.6880649901638419|
|    50%|-0.01392845608911...|4.529808944312057E-4|-0.01630454755484...|-0.01341902585471932|
|    75%|  0.6391356777594667|  0.6768263942589848|  0.6704488113096037|  0.6501401096039792|
|    max|   3.407902648447736|  3.8102699875673443|   3.5708

In [8]:
#Calclate some brief summary statistics
pop_data_sp.select(pop_data_sp.columns[23:]).summary().show()

23/05/08 15:03:26 WARN TaskSetManager: Stage 3 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


+-------+--------------------+--------------------+-------------------+
|summary|                 X24|                 X25|                  y|
+-------+--------------------+--------------------+-------------------+
|  count|                5000|                5000|               5000|
|   mean|-0.00498021898128...|-0.02020631205235034| -3.798446493633077|
| stddev|  0.9877367012402092|  1.0201279396655665| 234.20786791921896|
|    min|  -3.367035150216294| -3.4850827883691182| -884.2724915998847|
|    25%| -0.6889496650184208| -0.7074029537948439| -156.7858165392303|
|    50%|-0.01406311451878...|-0.01767028251457...|-1.7103445920178768|
|    75%|  0.6693079349083157|  0.6525044474585894| 158.57970199205099|
|    max|   3.499212619752443|  3.8085663482139127|  972.4118959873122|
+-------+--------------------+--------------------+-------------------+



## Linear Regression

Building a linear regression model.

In [28]:
# https://runawayhorse001.github.io/LearningApacheSpark/manipulation.html

#Vector Assmbler to turn features columns into a vector for the machine learning methods
vec_assembler = VectorAssembler(inputCols = pop_data_sp.columns[0:24],
               outputCol = "features")

# Construct the linear regression object
lin_reg = LinearRegression(labelCol = "y")

# Build a parameter grid for cross validation purposes
lin_reg_params = ParamGridBuilder()\
            .addGrid(lin_reg.maxIter,[10, 50, 100])\
            .addGrid(lin_reg.regParam, [0, 0.5, 1])\
            .addGrid(lin_reg.elasticNetParam, [0, 0.5, 1]).build()

In [26]:
# construct the pipeline for the linear regression
pipeline_lin_reg_1 =  Pipeline(stages = [vec_assembler, lin_reg])

In [11]:
# The train test split.
train_dat, test_dat = pop_data_sp.randomSplit(weights = [0.7, 0.3], seed = 424)

In [14]:
# Using cros validation to fit the model with the best hyperparameters.
cross_val_train_test = CrossValidator(estimator = pipeline_lin_reg_1,
                              estimatorParamMaps = lin_reg_params,
                              evaluator= RegressionEvaluator(labelCol = "y"),
                                    numFolds = 5)

Fit the model using cross validation on the training set.

In [16]:
lin_reg_model_fitted = cross_val_train_test.fit(train_dat)

23/05/08 15:07:00 WARN Instrumentation: [b021553c] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:00 WARN TaskSetManager: Stage 467 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:00 WARN TaskSetManager: Stage 468 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:00 WARN TaskSetManager: Stage 469 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:01 WARN Instrumentation: [53c7e2bb] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:01 WARN TaskSetManager: Stage 470 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:01 WARN TaskSetManager: Stage 471 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:01 WARN TaskSetMan

23/05/08 15:07:04 WARN TaskSetManager: Stage 522 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:04 WARN TaskSetManager: Stage 523 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:04 WARN Instrumentation: [ebd86e64] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:04 WARN TaskSetManager: Stage 524 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:04 WARN TaskSetManager: Stage 525 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:04 WARN TaskSetManager: Stage 526 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:04 WARN Instrumentation: [0edea628] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:04 WARN TaskSetMan

23/05/08 15:07:08 WARN TaskSetManager: Stage 577 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:08 WARN Instrumentation: [ccb3613c] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:08 WARN TaskSetManager: Stage 578 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:08 WARN TaskSetManager: Stage 579 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:08 WARN TaskSetManager: Stage 580 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:08 WARN Instrumentation: [782f222f] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:08 WARN TaskSetManager: Stage 581 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:08 WARN TaskSetMan

23/05/08 15:07:11 WARN TaskSetManager: Stage 630 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:11 WARN TaskSetManager: Stage 631 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:11 WARN Instrumentation: [d8534d82] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:11 WARN TaskSetManager: Stage 632 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:12 WARN TaskSetManager: Stage 633 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:12 WARN TaskSetManager: Stage 634 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:12 WARN Instrumentation: [2064dabd] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:12 WARN TaskSetMan

23/05/08 15:07:15 WARN Instrumentation: [4bfa2cf9] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:15 WARN TaskSetManager: Stage 686 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:15 WARN TaskSetManager: Stage 687 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:15 WARN TaskSetManager: Stage 688 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:15 WARN Instrumentation: [2f2390d4] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:15 WARN TaskSetManager: Stage 689 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:15 WARN TaskSetManager: Stage 690 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:15 WARN TaskSetMan

23/05/08 15:07:18 WARN TaskSetManager: Stage 742 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:18 WARN Instrumentation: [a28b914b] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 15:07:18 WARN TaskSetManager: Stage 743 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:18 WARN TaskSetManager: Stage 744 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:18 WARN TaskSetManager: Stage 745 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:18 WARN TaskSetManager: Stage 746 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:19 WARN TaskSetManager: Stage 747 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:1

23/05/08 15:07:22 WARN TaskSetManager: Stage 798 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 799 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 800 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 801 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 802 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 803 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:22 WARN TaskSetManager: Stage 804 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.

23/05/08 15:07:25 WARN TaskSetManager: Stage 852 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:25 WARN TaskSetManager: Stage 853 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:25 WARN TaskSetManager: Stage 854 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:25 WARN TaskSetManager: Stage 855 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:25 WARN TaskSetManager: Stage 856 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:25 WARN TaskSetManager: Stage 857 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 15:07:26 WARN TaskSetManager: Stage 858 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.

In [51]:
lin_reg_model_fitted.avgMetrics[1]

1.0043007822460508

Get the root mean squared error.

In [36]:
RegressionEvaluator(labelCol = "y").evaluate(lin_reg_model_fitted.transform(train_dat))

23/05/08 16:26:47 WARN TaskSetManager: Stage 6285 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


0.9946643918675739

Get RMSE for the test data.

In [37]:
RegressionEvaluator(labelCol = "y").evaluate(lin_reg_model_fitted.transform(test_dat))

23/05/08 16:26:49 WARN TaskSetManager: Stage 6286 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


1.0049702500587054

### PCA Linear Regression

Using PCA for dimensionality reduction before utilizing linear regression.

In [47]:
# PCA transformation of features vector to pcaFeat vector
pca_transformer = PCA(inputCol="features",outputCol = "pcaFeat")

# Linear regression object that takes pcaFeat as the features
lin_reg_2 = LinearRegression(featuresCol = "pcaFeat",labelCol = "y")

# Another pipeline for smooth estimator building
pipeline_lin_reg_2 =  Pipeline(stages = [vec_assembler,pca_transformer, lin_reg_2])

# building a new param grid with PCA hyperparameters.
lin_reg_2_params = ParamGridBuilder()\
            .addGrid(pca_transformer.k, [2, 4, 8])\ # estimator followed by hyperameter name, then values in a tuple
            .addGrid(lin_reg.maxIter,[10, 50, 100])\
            .addGrid(lin_reg.regParam, [0, 0.5, 1])\
            .addGrid(lin_reg.elasticNetParam, [0, 0.5, 1]).build()

In [48]:
# Setting up the cross validation object
pca_lin_reg_2 = CrossValidator(estimator = pipeline_lin_reg_2, # esitmator/pipeline
                              estimatorParamMaps = lin_reg_2_params, # parameter grid for pipeline/estimator
                              evaluator= RegressionEvaluator(labelCol = "y"),
                                    numFolds = 5)

In [49]:
# Fitting the linear regression model with PCA
lin_reg_model_fitted_pca = pca_lin_reg_2.fit(train_dat)

23/05/08 17:05:17 WARN TaskSetManager: Stage 22693 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:17 WARN TaskSetManager: Stage 22694 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:17 WARN TaskSetManager: Stage 22695 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:17 WARN TaskSetManager: Stage 22696 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:17 WARN TaskSetManager: Stage 22697 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:18 WARN Instrumentation: [88b69941] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 17:05:18 WARN TaskSetManager: Stage 22698 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/0

23/05/08 17:05:21 WARN Instrumentation: [3ae7aebc] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 17:05:21 WARN TaskSetManager: Stage 22746 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:21 WARN TaskSetManager: Stage 22747 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:22 WARN TaskSetManager: Stage 22748 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:22 WARN TaskSetManager: Stage 22749 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:22 WARN TaskSetManager: Stage 22750 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:22 WARN TaskSetManager: Stage 22751 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/0

23/05/08 17:05:25 WARN TaskSetManager: Stage 22797 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:25 WARN TaskSetManager: Stage 22798 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:25 WARN TaskSetManager: Stage 22799 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:25 WARN TaskSetManager: Stage 22800 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:25 WARN TaskSetManager: Stage 22801 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:25 WARN Instrumentation: [791797d8] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 17:05:25 WARN TaskSetManager: Stage 22802 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/0

23/05/08 17:05:28 WARN TaskSetManager: Stage 22851 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:28 WARN TaskSetManager: Stage 22852 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:28 WARN TaskSetManager: Stage 22853 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:28 WARN TaskSetManager: Stage 22854 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:28 WARN TaskSetManager: Stage 22855 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:28 WARN TaskSetManager: Stage 22856 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:29 WARN TaskSetManager: Stage 22857 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:05:31 WARN TaskSetManager: Stage 22907 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22908 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22909 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22910 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22911 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22912 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:05:32 WARN TaskSetManager: Stage 22913 contains a task of very large size (1164 KiB). The maximum recommended task siz

...

23/05/08 17:08:11 WARN Instrumentation: [76c72143] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 17:08:11 WARN TaskSetManager: Stage 25714 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:11 WARN TaskSetManager: Stage 25715 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:11 WARN TaskSetManager: Stage 25716 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:11 WARN TaskSetManager: Stage 25717 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:12 WARN TaskSetManager: Stage 25718 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:12 WARN TaskSetManager: Stage 25719 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/0

23/05/08 17:08:14 WARN TaskSetManager: Stage 25766 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:14 WARN TaskSetManager: Stage 25767 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:14 WARN TaskSetManager: Stage 25768 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:14 WARN TaskSetManager: Stage 25769 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:14 WARN Instrumentation: [748412cc] regParam is zero, which might cause numerical instability and overfitting.
23/05/08 17:08:14 WARN TaskSetManager: Stage 25770 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:14 WARN TaskSetManager: Stage 25771 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/0

23/05/08 17:08:17 WARN TaskSetManager: Stage 25819 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:17 WARN TaskSetManager: Stage 25820 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:17 WARN TaskSetManager: Stage 25821 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:17 WARN TaskSetManager: Stage 25822 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:17 WARN TaskSetManager: Stage 25823 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:18 WARN TaskSetManager: Stage 25824 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:18 WARN TaskSetManager: Stage 25825 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:08:20 WARN TaskSetManager: Stage 25875 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:20 WARN TaskSetManager: Stage 25876 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:20 WARN TaskSetManager: Stage 25877 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:20 WARN TaskSetManager: Stage 25878 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:20 WARN TaskSetManager: Stage 25879 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:20 WARN TaskSetManager: Stage 25880 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:21 WARN TaskSetManager: Stage 25881 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:08:24 WARN TaskSetManager: Stage 25931 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25932 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25933 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25934 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25935 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25936 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:08:24 WARN TaskSetManager: Stage 25937 contains a task of very large size (1164 KiB). The maximum recommended task siz

Get the RMSE for the training data.

In [50]:
RegressionEvaluator(labelCol = "y").evaluate(lin_reg_model_fitted_pca.transform(train_dat))

23/05/08 17:08:25 WARN TaskSetManager: Stage 25940 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


187.58183277963244

Get the RMSE for the testing data.

In [35]:
RegressionEvaluator(labelCol = "y").evaluate(lin_reg_model_fitted_pca.transform(test_dat))

23/05/08 16:26:40 WARN TaskSetManager: Stage 6284 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


180.23281371085415

## Gradient Boosted Tree

Using Gradient Boosted Trees next.

In [55]:
# Build the Gradient Boosted tree object
gbtRegress = GBTRegressor(labelCol = "y")

In [56]:
# constructing the pipeline
gbt_pipeline_1 = Pipeline(stages = [vec_assembler, gbtRegress])

In [58]:
# constructing the parameter grid
gbt_reg_params = ParamGridBuilder()\
            .addGrid(gbtRegress.maxIter,[5, 10, 20, 30])\
            .addGrid(gbtRegress.maxDepth, [5, 10, 15])\
            .addGrid(gbtRegress.featureSubsetStrategy, ["auto"])\
            .addGrid(gbtRegress.subsamplingRate, [0.2, 0.4, 0.6]).build()

In [59]:
# building cross validaiton object
gbt_cross_val = CrossValidator(estimator = gbt_pipeline_1,
                              estimatorParamMaps = gbt_reg_params,
                              evaluator= RegressionEvaluator(labelCol = "y"),
                                    numFolds = 5)

In [61]:
start_time_gbt = time.time()
gbt_model_fitted = gbt_cross_val.fit(train_dat)
end_time_gbt = time.time() - start_time_gbt

23/05/08 17:24:50 WARN TaskSetManager: Stage 25941 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25942 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25943 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25945 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25947 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25949 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:50 WARN TaskSetManager: Stage 25951 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:24:55 WARN TaskSetManager: Stage 26051 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26052 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26053 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26055 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26057 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26059 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:55 WARN TaskSetManager: Stage 26061 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:24:59 WARN TaskSetManager: Stage 26164 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26166 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26168 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26170 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26172 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26174 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:24:59 WARN TaskSetManager: Stage 26176 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:25:03 WARN TaskSetManager: Stage 26279 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:03 WARN TaskSetManager: Stage 26281 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:03 WARN TaskSetManager: Stage 26283 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:03 WARN TaskSetManager: Stage 26285 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:04 WARN TaskSetManager: Stage 26287 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:04 WARN TaskSetManager: Stage 26289 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:04 WARN TaskSetManager: Stage 26291 contains a task of very large size (1164 KiB). The maximum recommended task siz

23/05/08 17:25:08 WARN TaskSetManager: Stage 26394 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:08 WARN TaskSetManager: Stage 26396 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:08 WARN TaskSetManager: Stage 26398 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:08 WARN TaskSetManager: Stage 26400 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:08 WARN TaskSetManager: Stage 26402 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:09 WARN TaskSetManager: Stage 26404 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 17:25:09 WARN TaskSetManager: Stage 26406 contains a task of very large size (1165 KiB). The maximum recommended task siz

...

23/05/08 18:06:04 WARN DAGScheduler: Broadcasting large task binary with size 4.0 MiB
23/05/08 18:06:04 WARN TaskSetManager: Stage 85226 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:04 WARN DAGScheduler: Broadcasting large task binary with size 4.0 MiB
23/05/08 18:06:04 WARN TaskSetManager: Stage 85228 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:04 WARN DAGScheduler: Broadcasting large task binary with size 4.0 MiB
23/05/08 18:06:04 WARN TaskSetManager: Stage 85230 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:04 WARN DAGScheduler: Broadcasting large task binary with size 4.0 MiB
23/05/08 18:06:04 WARN TaskSetManager: Stage 85232 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:05 WARN DAGScheduler: Broadcasting large task binary with siz

23/05/08 18:06:10 WARN DAGScheduler: Broadcasting large task binary with size 4.4 MiB
23/05/08 18:06:10 WARN TaskSetManager: Stage 85300 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:10 WARN DAGScheduler: Broadcasting large task binary with size 4.4 MiB
23/05/08 18:06:10 WARN TaskSetManager: Stage 85302 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:10 WARN DAGScheduler: Broadcasting large task binary with size 4.5 MiB
23/05/08 18:06:10 WARN TaskSetManager: Stage 85304 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:10 WARN DAGScheduler: Broadcasting large task binary with size 4.5 MiB
23/05/08 18:06:10 WARN TaskSetManager: Stage 85306 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:11 WARN DAGScheduler: Broadcasting large task binary with siz

23/05/08 18:06:14 WARN TaskSetManager: Stage 85387 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85389 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85391 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85393 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85395 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85397 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:14 WARN TaskSetManager: Stage 85399 contains a task of very large size (1165 KiB). The maximum recommended task siz

23/05/08 18:06:16 WARN TaskSetManager: Stage 85505 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85507 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85509 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85511 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85513 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85515 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:16 WARN TaskSetManager: Stage 85517 contains a task of very large size (1165 KiB). The maximum recommended task siz

23/05/08 18:06:18 WARN TaskSetManager: Stage 85621 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85623 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85625 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85627 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85629 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85631 contains a task of very large size (1165 KiB). The maximum recommended task size is 1000 KiB.
23/05/08 18:06:18 WARN TaskSetManager: Stage 85633 contains a task of very large size (1165 KiB). The maximum recommended task siz

In [62]:
# Time taken to train and select the hyperparameters
end_time_gbt

2488.3915481567383

Get the RMSE for the gradient boosted trees on the training set.

In [63]:
RegressionEvaluator(labelCol = "y").evaluate(gbt_model_fitted.transform(train_dat))

23/05/08 18:06:18 WARN TaskSetManager: Stage 85645 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


73.33315562510478

Get the RMSE for the gradient boosted trees on the test set.

In [64]:
RegressionEvaluator(labelCol = "y").evaluate(gbt_model_fitted.transform(test_dat))

23/05/08 18:06:19 WARN TaskSetManager: Stage 85646 contains a task of very large size (1164 KiB). The maximum recommended task size is 1000 KiB.


105.2923947531027